# 제품 이상여부 판별 프로젝트


## 1. 데이터 불러오기


### 필수 라이브러리


In [1]:
import os
from pprint import pprint

import numpy as np
import pandas as pd
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import (
    accuracy_score,
    classification_report,
    confusion_matrix,
    f1_score,
    precision_score,
    recall_score,
)
from sklearn.model_selection import train_test_split
from tqdm import tqdm

### 데이터 읽어오기


In [2]:
ROOT_DIR = "data"

# 랜덤 시드 설정
RANDOM_STATE = 42
# Load data
train_data = pd.read_csv(os.path.join(ROOT_DIR, "train.csv"))
train_data

Wip Line_Dam Process Desc._Dam     Equipment_Dam Model.Suffix_Dam  \
0          IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334505   
1          IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334505   
2          IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
3          IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
4          IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
...            ...               ...               ...              ...   
40501      IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
40502      IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
40503      IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
40504      IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
40505      IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   

      Workorder_Dam  Insp. Seq No._Dam Insp Judge Code_Dam  \
0        4F1XA938-1                  1                  OK   
1        3KPM0016-2                  1                  OK   
2        4E1X9167-1                  1                  OK   
3        3K1X0057-1                  1                  OK   
4        3HPM0007-1                  1                  OK   
...             ...                ...                 ...   
40501    3J1XF434-2                  1                  OK   
40502    4E1XC796-1                  1                  OK   
40503    4C1XD438-1                  1                  OK   
40504    3I1XA258-1                  1                  OK   
40505    3G1XA501-1                  1                  OK   

       CURE END POSITION X Collect Result_Dam  \
0                                       240.0   
1                                       240.0   
2                                      1000.0   
3                                      1000.0   
4                                       240.0   
...                                       ...   
40501                                   240.0   
40502                                  1000.0   
40503                                   240.0   
40504                                  1000.0   
40505                                   240.0   

       CURE END POSITION X Unit Time_Dam  CURE END POSITION X Judge Value_Dam  \
0                                    NaN                                  NaN   
1                                    NaN                                  NaN   
2                                    NaN                                  NaN   
3                                    NaN                                  NaN   
4                                    NaN                                  NaN   
...                                  ...                                  ...   
40501                                NaN                                  NaN   
40502                                NaN                                  NaN   
40503                                NaN                                  NaN   
40504                                NaN                                  NaN   
40505                                NaN                                  NaN   

       ...  Production Qty Collect Result_Fill2  \
0      ...                                    7   
1      ...                                  185   
2      ...                                   10   
3      ...                                  268   
4      ...                                  121   
...    ...                                  ...   
40501  ...                                  318   
40502  ...                                   14   
40503  ...                                    1   
40504  ...                                  117   
40505  ...                                  320   

       Production Qty Unit Time_Fill2  Production Qty Judge Value_Fill2  \
0                                 NaN                               NaN   
1                                 N

In [3]:
# Drop columns with more than half of the values missing
drop_cols = []
for column in train_data.columns:
    if (train_data[column].notnull().sum() // 2) < train_data[
        column
    ].isnull().sum():
        drop_cols.append(column)
train_data = train_data.drop(drop_cols, axis=1)

train_data

Wip Line_Dam Process Desc._Dam     Equipment_Dam Model.Suffix_Dam  \
0          IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334505   
1          IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334505   
2          IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
3          IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
4          IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
...            ...               ...               ...              ...   
40501      IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
40502      IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
40503      IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
40504      IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
40505      IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   

      Workorder_Dam  Insp. Seq No._Dam Insp Judge Code_Dam  \
0        4F1XA938-1                  1                  OK   
1        3KPM0016-2                  1                  OK   
2        4E1X9167-1                  1                  OK   
3        3K1X0057-1                  1                  OK   
4        3HPM0007-1                  1                  OK   
...             ...                ...                 ...   
40501    3J1XF434-2                  1                  OK   
40502    4E1XC796-1                  1                  OK   
40503    4C1XD438-1                  1                  OK   
40504    3I1XA258-1                  1                  OK   
40505    3G1XA501-1                  1                  OK   

       CURE END POSITION X Collect Result_Dam  \
0                                       240.0   
1                                       240.0   
2                                      1000.0   
3                                      1000.0   
4                                       240.0   
...                                       ...   
40501                                   240.0   
40502                                  1000.0   
40503                                   240.0   
40504                                  1000.0   
40505                                   240.0   

       CURE END POSITION Z Collect Result_Dam  \
0                                         2.5   
1                                         2.5   
2                                        12.5   
3                                        12.5   
4                                         2.5   
...                                       ...   
40501                                     2.5   
40502                                    12.5   
40503                                     2.5   
40504                                    12.5   
40505                                     2.5   

       CURE END POSITION Θ Collect Result_Dam  ...  \
0                                         -90  ...   
1                                         -90  ...   
2                                          90  ...   
3                                          90  ...   
4                                         -90  ...   
...                                       ...  ...   
40501                                     -90  ...   
40502                                      90  ...   
40503                                     -90  ...   
40504                                      90  ...   
40505                                     -90  ...   

       Head Clean Position Z Collect Result_Fill2  \
0                                            50.0   
1                                            91.8   
2                                            50.0   
3                                            91.8   
4                                            91.8   
...                                           ...   
40501                                        91.8   
40502                                        50.0   
40503                                        50.0   
405

In [4]:
# 각 열의 NaN 값 개수 계산
nan_counts = train_data.isnull().sum()

# NaN 값이 있는 열들만 필터링
nan_columns = nan_counts[nan_counts > 0]

nan_columns

HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam      12766
HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1    12766
HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill2    12766
dtype: int64

In [5]:
# 각 열의 NaN 값이 있는 행을 표시
nan_dam = train_data['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam'].isnull()
nan_fill1 = train_data['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1'].isnull()
nan_fill2 = train_data['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill2'].isnull()

# 세 열의 NaN 값이 모두 같은 행에서 발생했는지 확인
nan_same_rows = nan_dam & nan_fill1 & nan_fill2

# NaN 값이 동일한 행의 개수 확인
num_same_nan_rows = nan_same_rows.sum()

# 결과 출력
print(f"세 열에서 NaN 값이 동일한 행의 개수: {num_same_nan_rows}")
print(f"세 열에서 NaN 값이 동일한 행:\n{train_data[nan_same_rows]}")

세 열에서 NaN 값이 동일한 행의 개수: 12766
세 열에서 NaN 값이 동일한 행:
      Wip Line_Dam Process Desc._Dam     Equipment_Dam Model.Suffix_Dam  \
0          IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334505   
12         IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
13         IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
18         IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
24         IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334507   
...            ...               ...               ...              ...   
40485      IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
40491      IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
40492      IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
40500      IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
40502      IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   

       Workorder_Dam  Insp. Seq No._Dam Insp Judg

In [6]:
# 열 목록을 정의
required_columns = [
    'HEAD NORMAL COORDINATE X AXIS(Stage1) Judge Value_Dam',
    'HEAD NORMAL COORDINATE X AXIS(Stage1) Judge Value_Fill1',
    'HEAD NORMAL COORDINATE X AXIS(Stage1) Judge Value_Fill2',
    'GMES_ORIGIN_INSP_JUDGE_CODE Collect Result_AutoClave',
    'GMES_ORIGIN_INSP_JUDGE_CODE Judge Value_AutoClave'
]

# 존재하는 열들만 필터링
existing_columns = [col for col in required_columns if col in train_data.columns]

# 존재하는 열들 출력
print("존재하는 열들:", existing_columns)

존재하는 열들: []


In [7]:
# Model.Suffix의 값이 공정에 따라 같은지 다른지 비교할 열 리스트
suffix_columns = [
    'Model.Suffix_Dam',
    'Model.Suffix_Fill1',
    'Model.Suffix_Fill2',
    'Model.Suffix_AutoClave'
]

# 각 행에 대해 모든 비교 열의 값이 동일한지 확인
all_equal = train_data[suffix_columns].nunique(axis=1) == 1

# 동일한 값을 가진 행만 필터링하여 네 개의 열만 선택
equal_rows = train_data.loc[all_equal, suffix_columns]

# 동일한 값을 가진 행의 개수와 결과 출력
print(f"동일한 값을 가진 행의 개수: {len(equal_rows)}")
print(equal_rows)

동일한 값을 가진 행의 개수: 40506
      Model.Suffix_Dam Model.Suffix_Fill1 Model.Suffix_Fill2  \
0          AJX75334505        AJX75334505        AJX75334505   
1          AJX75334505        AJX75334505        AJX75334505   
2          AJX75334501        AJX75334501        AJX75334501   
3          AJX75334501        AJX75334501        AJX75334501   
4          AJX75334501        AJX75334501        AJX75334501   
...                ...                ...                ...   
40501      AJX75334501        AJX75334501        AJX75334501   
40502      AJX75334501        AJX75334501        AJX75334501   
40503      AJX75334501        AJX75334501        AJX75334501   
40504      AJX75334501        AJX75334501        AJX75334501   
40505      AJX75334501        AJX75334501        AJX75334501   

      Model.Suffix_AutoClave  
0                AJX75334505  
1                AJX75334505  
2                AJX75334501  
3                AJX75334501  
4                AJX75334501  
...                   

In [8]:
# Workorder의 값이 공정에 따라 같은지 다른지 비교할 열 리스트
suffix_columns = [
    'Workorder_Dam',
    'Workorder_Fill1',
    'Workorder_Fill2',
    'Workorder_AutoClave'
]

# 각 행에 대해 모든 비교 열의 값이 동일한지 확인
all_equal = train_data[suffix_columns].nunique(axis=1) == 1

# 동일한 값을 가진 행만 필터링하여 네 개의 열만 선택
equal_rows = train_data.loc[all_equal, suffix_columns]

# 동일한 값을 가진 행의 개수와 결과 출력
print(f"동일한 값을 가진 행의 개수: {len(equal_rows)}")
print(equal_rows)

동일한 값을 가진 행의 개수: 40506
      Workorder_Dam Workorder_Fill1 Workorder_Fill2 Workorder_AutoClave
0        4F1XA938-1      4F1XA938-1      4F1XA938-1          4F1XA938-1
1        3KPM0016-2      3KPM0016-2      3KPM0016-2          3KPM0016-2
2        4E1X9167-1      4E1X9167-1      4E1X9167-1          4E1X9167-1
3        3K1X0057-1      3K1X0057-1      3K1X0057-1          3K1X0057-1
4        3HPM0007-1      3HPM0007-1      3HPM0007-1          3HPM0007-1
...             ...             ...             ...                 ...
40501    3J1XF434-2      3J1XF434-2      3J1XF434-2          3J1XF434-2
40502    4E1XC796-1      4E1XC796-1      4E1XC796-1          4E1XC796-1
40503    4C1XD438-1      4C1XD438-1      4C1XD438-1          4C1XD438-1
40504    3I1XA258-1      3I1XA258-1      3I1XA258-1          3I1XA258-1
40505    3G1XA501-1      3G1XA501-1      3G1XA501-1          3G1XA501-1

[40506 rows x 4 columns]


In [9]:
# 삭제할 열 리스트
columns_to_drop = [
        'Model.Suffix_Fill1', 'Model.Suffix_Fill2', 'Model.Suffix_AutoClave', 
        'Workorder_Fill1', 'Workorder_Fill2', 'Workorder_AutoClave'
]

# 열 삭제
train_data = train_data.drop(columns=columns_to_drop)

# 열 이름 변경
train_data = train_data.rename(columns={
    'Model.Suffix_Dam': 'Model.Suffix',
    'Workorder_Dam': 'Workorder'
})

train_data

Wip Line_Dam Process Desc._Dam     Equipment_Dam Model.Suffix  \
0          IVI-OB6     Dam Dispenser  Dam dispenser #1  AJX75334505   
1          IVI-OB6     Dam Dispenser  Dam dispenser #1  AJX75334505   
2          IVI-OB6     Dam Dispenser  Dam dispenser #2  AJX75334501   
3          IVI-OB6     Dam Dispenser  Dam dispenser #2  AJX75334501   
4          IVI-OB6     Dam Dispenser  Dam dispenser #1  AJX75334501   
...            ...               ...               ...          ...   
40501      IVI-OB6     Dam Dispenser  Dam dispenser #1  AJX75334501   
40502      IVI-OB6     Dam Dispenser  Dam dispenser #2  AJX75334501   
40503      IVI-OB6     Dam Dispenser  Dam dispenser #1  AJX75334501   
40504      IVI-OB6     Dam Dispenser  Dam dispenser #2  AJX75334501   
40505      IVI-OB6     Dam Dispenser  Dam dispenser #1  AJX75334501   

        Workorder  Insp. Seq No._Dam Insp Judge Code_Dam  \
0      4F1XA938-1                  1                  OK   
1      3KPM0016-2                  1                  OK   
2      4E1X9167-1                  1                  OK   
3      3K1X0057-1                  1                  OK   
4      3HPM0007-1                  1                  OK   
...           ...                ...                 ...   
40501  3J1XF434-2                  1                  OK   
40502  4E1XC796-1                  1                  OK   
40503  4C1XD438-1                  1                  OK   
40504  3I1XA258-1                  1                  OK   
40505  3G1XA501-1                  1                  OK   

       CURE END POSITION X Collect Result_Dam  \
0                                       240.0   
1                                       240.0   
2                                      1000.0   
3                                      1000.0   
4                                       240.0   
...                                       ...   
40501                                   240.0   
40502                                  1000.0   
40503                                   240.0   
40504                                  1000.0   
40505                                   240.0   

       CURE END POSITION Z Collect Result_Dam  \
0                                         2.5   
1                                         2.5   
2                                        12.5   
3                                        12.5   
4                                         2.5   
...                                       ...   
40501                                     2.5   
40502                                    12.5   
40503                                     2.5   
40504                                    12.5   
40505                                     2.5   

       CURE END POSITION Θ Collect Result_Dam  ...  \
0                                         -90  ...   
1                                         -90  ...   
2                                          90  ...   
3                                          90  ...   
4                                         -90  ...   
...                                       ...  ...   
40501                                     -90  ...   
40502                                      90  ...   
40503                                     -90  ...   
40504                                      90  ...   
40505                                     -90  ...   

       Head Clean Position Z Collect Result_Fill2  \
0                                            50.0   
1                                            91.8   
2                                            50.0   
3                                            91.8   
4                                            91.8   
...                                           ...   
40501                                        91.8   
40502                                        50.0   
40503                                        50.0   
40504                                        91.8   
40505                 

In [10]:
# 모든 행이 동일한 값을 가지는 열을 찾고, 그 값을 함께 저장
constant_columns = {col: train_data[col].iloc[0] for col in train_data.columns if train_data[col].nunique() == 1}

# 데이터 프레임에서 해당 열 삭제
train_data = train_data.drop(columns=constant_columns.keys())

# 삭제된 열의 개수 출력
print(f"삭제된 열의 개수: {len(constant_columns)}")

# 삭제된 열과 그 값을 한 줄에 하나씩 출력
print("삭제된 열과 값:")
for col, value in constant_columns.items():
    print(f"{col}: {value}")

train_data

삭제된 열의 개수: 35
삭제된 열과 값:
Wip Line_Dam: IVI-OB6
Process Desc._Dam: Dam Dispenser
Insp. Seq No._Dam: 1
Insp Judge Code_Dam: OK
CURE STANDBY POSITION X Collect Result_Dam: 1150
CURE STANDBY POSITION Z Collect Result_Dam: 33.5
CURE STANDBY POSITION Θ Collect Result_Dam: 0
CURE START POSITION Z Collect Result_Dam: 33.5
Wip Line_AutoClave: IVI-OB6
Process Desc._AutoClave: Auto Clave Out
Equipment_AutoClave: Auto Clave Out
Insp. Seq No._AutoClave: 1
Insp Judge Code_AutoClave: OK
1st Pressure Judge Value_AutoClave: OK
2nd Pressure Judge Value_AutoClave: OK
3rd Pressure Judge Value_AutoClave: OK
Wip Line_Fill1: IVI-OB6
Process Desc._Fill1: Fill1 Dispenser
Insp. Seq No._Fill1: 1
Insp Judge Code_Fill1: OK
Wip Line_Fill2: IVI-OB6
Process Desc._Fill2: Fill2 Dispenser
Insp. Seq No._Fill2: 1
Insp Judge Code_Fill2: OK
CURE END POSITION Θ Collect Result_Fill2: -90
CURE STANDBY POSITION X Collect Result_Fill2: 1020
CURE STANDBY POSITION Θ Collect Result_Fill2: 0
CURE START POSITION Θ Collect Result_Fill2

Equipment_Dam Model.Suffix   Workorder  \
0      Dam dispenser #1  AJX75334505  4F1XA938-1   
1      Dam dispenser #1  AJX75334505  3KPM0016-2   
2      Dam dispenser #2  AJX75334501  4E1X9167-1   
3      Dam dispenser #2  AJX75334501  3K1X0057-1   
4      Dam dispenser #1  AJX75334501  3HPM0007-1   
...                 ...          ...         ...   
40501  Dam dispenser #1  AJX75334501  3J1XF434-2   
40502  Dam dispenser #2  AJX75334501  4E1XC796-1   
40503  Dam dispenser #1  AJX75334501  4C1XD438-1   
40504  Dam dispenser #2  AJX75334501  3I1XA258-1   
40505  Dam dispenser #1  AJX75334501  3G1XA501-1   

       CURE END POSITION X Collect Result_Dam  \
0                                       240.0   
1                                       240.0   
2                                      1000.0   
3                                      1000.0   
4                                       240.0   
...                                       ...   
40501                                   240.0   
40502                                  1000.0   
40503                                   240.0   
40504                                  1000.0   
40505                                   240.0   

       CURE END POSITION Z Collect Result_Dam  \
0                                         2.5   
1                                         2.5   
2                                        12.5   
3                                        12.5   
4                                         2.5   
...                                       ...   
40501                                     2.5   
40502                                    12.5   
40503                                     2.5   
40504                                    12.5   
40505                                     2.5   

       CURE END POSITION Θ Collect Result_Dam  CURE SPEED Collect Result_Dam  \
0                                         -90                            100   
1                                         -90                             70   
2                                          90                             85   
3                                          90                             70   
4                                         -90                             70   
...                                       ...                            ...   
40501                                     -90                             70   
40502                                      90                            100   
40503                                     -90                            100   
40504                                      90                             70   
40505                                     -90                             70   

       CURE START POSITION X Collect Result_Dam  \
0                                          1030   
1                                          1030   
2                                           280   
3                                           280   
4                                          1030   
...                                         ...   
40501                                      1030   
40502                                       280   
40503                                      1030   
40504                                       280   
40505                                      1030   

       CURE START POSITION Θ Collect Result_Dam  \
0                                           -90   
1                                           -90   
2                                            90   
3                                            90   
4                                           -90   
...                                         ...   
40501                                       -90   
40502                                        90   
40503                                       -90   
40504                                        90   
40505                                       -90   

       DISCHARGED SP

In [11]:
# 열 이름 정의
target_column = 'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam'

# 열의 값들 확인
if target_column not in train_data.columns:
    raise ValueError(f"열 '{target_column}'이(가) 데이터프레임에 없습니다.")

# 고유한 값 추출
unique_values = train_data[target_column].unique()

# 고유한 값들을 포함한 DataFrame 생성
unique_values_df = pd.DataFrame(unique_values, columns=[target_column])

# 결측치와 문자열 포함 모든 고유 값 출력
print(f"'{target_column}' 열의 고유한 값들:")
print(unique_values_df)

# 추가로 결측치와 특정 값('OK')의 존재 여부 확인
nan_count = train_data[target_column].isna().sum()
ok_count = (train_data[target_column] == 'OK').sum()

print(f"\n결측치(NaN) 개수: {nan_count}")
print(f"'OK' 값 개수: {ok_count}")

'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam' 열의 고유한 값들:
  HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam
0                                                NaN      
1                                              550.3      
2                                                 OK      
3                                              162.4      
4                                                549      
5                                              549.5      
6                                                550      
7                                              548.5      

결측치(NaN) 개수: 12766
'OK' 값 개수: 11293


In [12]:
data = train_data.copy()

In [13]:
# # 제거할 열 리스트
columns_to_drop = ['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam', 
                   'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1', 
                   'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill2']
#   'WorkMode Collect Result_Dam', 'WorkMode Collect Result_Fill1', 'WorkMode Collect Result_Fill2'
# # 지정한 열 제거
data = data.drop(columns=columns_to_drop)

In [14]:
from sklearn.preprocessing import LabelEncoder
from sklearn.compose import make_column_transformer
from sklearn.preprocessing import OrdinalEncoder
from sklearn.pipeline import Pipeline

# 범주형 열을 선택하여 인코딩 수행
categorical_features = ['Equipment_Dam', 'Equipment_Fill1', 'Equipment_Fill2', 'Chamber Temp. Judge Value_AutoClave', 'Model.Suffix', 'Workorder']

# OrdinalEncoder 인스턴스 생성
encoder = OrdinalEncoder()

# 범주형 열에 대해서만 인코딩 수행
data[categorical_features] = encoder.fit_transform(data[categorical_features])

# 인코딩된 데이터프레임 확인
data

Equipment_Dam  Model.Suffix  Workorder  \
0                0.0           3.0      657.0   
1                0.0           3.0      283.0   
2                1.0           0.0      589.0   
3                1.0           0.0      251.0   
4                0.0           0.0      142.0   
...              ...           ...        ...   
40501            0.0           0.0      238.0   
40502            1.0           0.0      643.0   
40503            0.0           0.0      540.0   
40504            1.0           0.0      164.0   
40505            0.0           0.0       46.0   

       CURE END POSITION X Collect Result_Dam  \
0                                       240.0   
1                                       240.0   
2                                      1000.0   
3                                      1000.0   
4                                       240.0   
...                                       ...   
40501                                   240.0   
40502                                  1000.0   
40503                                   240.0   
40504                                  1000.0   
40505                                   240.0   

       CURE END POSITION Z Collect Result_Dam  \
0                                         2.5   
1                                         2.5   
2                                        12.5   
3                                        12.5   
4                                         2.5   
...                                       ...   
40501                                     2.5   
40502                                    12.5   
40503                                     2.5   
40504                                    12.5   
40505                                     2.5   

       CURE END POSITION Θ Collect Result_Dam  CURE SPEED Collect Result_Dam  \
0                                         -90                            100   
1                                         -90                             70   
2                                          90                             85   
3                                          90                             70   
4                                         -90                             70   
...                                       ...                            ...   
40501                                     -90                             70   
40502                                      90                            100   
40503                                     -90                            100   
40504                                      90                             70   
40505                                     -90                             70   

       CURE START POSITION X Collect Result_Dam  \
0                                          1030   
1                                          1030   
2                                           280   
3                                           280   
4                                          1030   
...                                         ...   
40501                                      1030   
40502                                       280   
40503                                      1030   
40504                                       280   
40505                                      1030   

       CURE START POSITION Θ Collect Result_Dam  \
0                                           -90   
1                                           -90   
2                                            90   
3                                            90   
4                                           -90   
...                                         ...   
40501                                       -90   
40502                                        90   
40503                                       -90   
40504                                        90   
40505                                       -90   

       DISCHARGED SPEED OF RESIN Collect Result_Dam  

In [15]:
# 각 범주에 대한 인코딩 값 확인
for feature, categories in zip(categorical_features, encoder.categories_):
    print(f"Feature: {feature}")
    for category, index in zip(categories, range(len(categories))):
        print(f"  {category}: {index}")

Feature: Equipment_Dam
  Dam dispenser #1: 0
  Dam dispenser #2: 1
Feature: Equipment_Fill1
  Fill1 dispenser #1: 0
  Fill1 dispenser #2: 1
Feature: Equipment_Fill2
  Fill2 dispenser #1: 0
  Fill2 dispenser #2: 1
Feature: Chamber Temp. Judge Value_AutoClave
  NG: 0
  OK: 1
Feature: Model.Suffix
  AJX75334501: 0
  AJX75334502: 1
  AJX75334503: 2
  AJX75334505: 3
  AJX75334506: 4
  AJX75334507: 5
  AJX75334508: 6
Feature: Workorder
  3F1X5847-2: 0
  3F1X9643-1: 1
  3F1X9644-1: 2
  3F1X9648-1: 3
  3F1X9648-2: 4
  3F1XA350-1: 5
  3F1XA351-1: 6
  3F1XB560-1: 7
  3F1XC376-1: 8
  3F1XC414-1: 9
  3F1XC414-2: 10
  3F1XC600-1: 11
  3F1XC781-1: 12
  3FPM0081-1: 13
  3FPM0085-1: 14
  3FPXX064-0003: 15
  3G1X4501-1: 16
  3G1X4502-2: 17
  3G1X4503-1: 18
  3G1X8290-1: 19
  3G1X8293-1: 20
  3G1X8295-1: 21
  3G1X8296-1: 22
  3G1X8297-1: 23
  3G1X8297-2: 24
  3G1X8298-1: 25
  3G1X8298-2: 26
  3G1X8299-1: 27
  3G1X8300-1: 28
  3G1X8300-2: 29
  3G1X8303-1: 30
  3G1X8646-1: 31
  3G1X8646-2: 32
  3G1X8647-1

In [16]:
# 문자열 타입인 열들의 이름과 데이터 타입 출력
string_columns = data.select_dtypes(include='object')
string_columns.dtypes

target    object
dtype: object

##  train/val split,  df_abnormal 구분, 언더샘플링,  장비 구분

In [17]:
from sklearn.model_selection import train_test_split



# train/val split
df_train, df_val = train_test_split(
    data,
    test_size=0.3,
    stratify=data["target"],
    random_state=RANDOM_STATE,
)

In [18]:
categorical_features = ['Equipment_Dam', 'Equipment_Fill1', 'Equipment_Fill2']
# 세 가지 조건: 열 간 값이 다르면 불량으로 분류
condition_receip = (
    (df_train['Receip No Collect Result_Dam'] != df_train['Receip No Collect Result_Fill1']) |
    (df_train['Receip No Collect Result_Dam'] != df_train['Receip No Collect Result_Fill2']) |
    (df_train['Receip No Collect Result_Fill1'] != df_train['Receip No Collect Result_Fill2'])
)

condition_production_qty = (
    (df_train['Production Qty Collect Result_Dam'] != df_train['Production Qty Collect Result_Fill1']) |
    (df_train['Production Qty Collect Result_Dam'] != df_train['Production Qty Collect Result_Fill2']) |
    (df_train['Production Qty Collect Result_Fill1'] != df_train['Production Qty Collect Result_Fill2'])
)

# 장비가 다르면 불량으로 분류
equip1 = df_train[categorical_features].eq(0).all(axis=1)
equip2 = df_train[categorical_features].eq(1).all(axis=1)
condition_equip_different = ~equip1 & ~equip2

# 네 조건 중 하나라도 만족하면 불량으로 분류
condition_abnormal = condition_receip | condition_production_qty | condition_equip_different

# 불량 데이터와 정상 데이터로 분리
df_abnormal = df_train[condition_abnormal]  # 불량으로 분류할 데이터
df_filtered = df_train[~condition_abnormal]  # 모델1, 2로 학습할 데이터


# 결과 확인
print(f"불량 데이터: {len(df_abnormal)} 행")
print(f"정상 데이터: {len(df_filtered)} 행")

불량 데이터: 62 행
정상 데이터: 28292 행


In [19]:
df_abnormal['target'].value_counts()

target
AbNormal    62
Name: count, dtype: int64

In [20]:
print(df_train.shape)
print(df_filtered.shape)

(28354, 137)
(28292, 137)


In [21]:
normal_ratio = 8.0  # 1.0 means 1:1 ratio

df_normal = df_filtered[df_filtered["target"] == "Normal"]
df_abnormal = df_filtered[df_filtered["target"] == "AbNormal"]

num_normal = len(df_normal)
num_abnormal = len(df_abnormal)
print(f"  Total: Normal: {num_normal}, AbNormal: {num_abnormal}")

df_normal = df_normal.sample(n=int(num_abnormal * normal_ratio), replace=False, random_state=RANDOM_STATE)
df_concat = pd.concat([df_normal, df_abnormal], axis=0).reset_index(drop=True)
df_concat.value_counts("target")

  Total: Normal: 26709, AbNormal: 1583


target
Normal      12664
AbNormal     1583
Name: count, dtype: int64

In [22]:
# 정상 데이터에서 장비별로 데이터 분리
df_model1 = df_concat[df_concat[categorical_features].eq(0).all(axis=1)]
df_model2 = df_concat[df_concat[categorical_features].eq(1).all(axis=1)]

print(f"Equipment #1 데이터: {len(df_model1)} 행")
print(f"Equipment #2 데이터: {len(df_model2)} 행")

Equipment #1 데이터: 8870 행
Equipment #2 데이터: 5377 행


In [23]:
# 데이터와 타겟 분리
X_model1 = df_model1.drop(columns='target')
y_model1 = df_model1['target']
X_model2 = df_model2.drop(columns='target')
y_model2 = df_model2['target']

##  RandomForest

In [28]:
# 모델 훈련

model1 = RandomForestClassifier(random_state=RANDOM_STATE)
model1.fit(X_model1, y_model1)

model2 = RandomForestClassifier(random_state=RANDOM_STATE)
model2.fit(X_model2, y_model2)

RandomForestClassifier(random_state=42)

In [29]:
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestClassifier

param_grid = {
    'n_estimators': [100, 200, 500],  # 적절한 트리 수
    'max_depth': [30, 50, None],  # 깊이를 넓게 설정
    'min_samples_split': [10, 20],  # 분할을 더 자유롭게 설정
    'min_samples_leaf': [1, 2, 4, 8, 16],  # 리프 노드 최소 샘플 수
    'criterion': ['gini']
    #'max_features': ['auto', 'sqrt', 'log2']  # 다양한 특징 선택 방법
}

model1 = RandomForestClassifier(random_state=RANDOM_STATE)

model1_rf_grid_search = GridSearchCV(estimator=model1, param_grid=param_grid, 
                           scoring='f1_weighted', cv=5, verbose=2, n_jobs=-1)

model1_rf_grid_search.fit(X_model1, y_model1)

Fitting 5 folds for each of 90 candidates, totalling 450 fits


KeyboardInterrupt: 

In [26]:
print("Best1 parameters found: ", model1_rf_grid_search.best_params_)
print("Best1 parameters score: ", model1_rf_grid_search.best_score_)

Best1 parameters found:  {'criterion': 'gini', 'max_depth': 30, 'min_samples_leaf': 1, 'min_samples_split': 10, 'n_estimators': 200}
Best1 parameters score:  0.8406886321529863


In [27]:
model2 = RandomForestClassifier(random_state=RANDOM_STATE)
                                
model2_rf_grid_search = GridSearchCV(estimator=model2, param_grid=param_grid, 
                           scoring='f1_weighted', cv=5, verbose=2, n_jobs=-1)

model2_rf_grid_search.fit(X_model2, y_model2)

Fitting 5 folds for each of 90 candidates, totalling 450 fits


GridSearchCV(cv=5, estimator=RandomForestClassifier(random_state=42), n_jobs=-1,
             param_grid={'criterion': ['gini'], 'max_depth': [30, 50, None],
                         'min_samples_leaf': [1, 2, 4, 8, 16],
                         'min_samples_split': [10, 20],
                         'n_estimators': [100, 200, 500]},
             scoring='f1_weighted', verbose=2)

In [28]:
print("Best2 parameters found: ", model2_rf_grid_search.best_params_)
print("Best2 parameters score: ", model2_rf_grid_search.best_score_)

Best2 parameters found:  {'criterion': 'gini', 'max_depth': 30, 'min_samples_leaf': 1, 'min_samples_split': 10, 'n_estimators': 100}
Best2 parameters score:  0.8613063150866914


In [29]:
model1_rf = RandomForestClassifier(**model1_rf_grid_search.best_params_, random_state=RANDOM_STATE, class_weight='balanced')
model1_rf.fit(X_model1, y_model1)
model2_rf = RandomForestClassifier(**model2_rf_grid_search.best_params_, random_state=RANDOM_STATE, class_weight='balanced')
model2_rf.fit(X_model2, y_model2)

RandomForestClassifier(class_weight='balanced', max_depth=30,
                       min_samples_split=10, random_state=42)

###  RandomForest 모델 평가

In [30]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, f1_score

y_val = df_val["target"]

# 세 가지 조건: 열 간 값이 다르면 불량으로 분류
condition_receip = (
    (df_val['Receip No Collect Result_Dam'] != df_val['Receip No Collect Result_Fill1']) |
    (df_val['Receip No Collect Result_Dam'] != df_val['Receip No Collect Result_Fill2']) |
    (df_val['Receip No Collect Result_Fill1'] != df_val['Receip No Collect Result_Fill2'])
)

condition_production_qty = (
    (df_val['Production Qty Collect Result_Dam'] != df_val['Production Qty Collect Result_Fill1']) |
    (df_val['Production Qty Collect Result_Dam'] != df_val['Production Qty Collect Result_Fill2']) |
    (df_val['Production Qty Collect Result_Fill1'] != df_val['Production Qty Collect Result_Fill2'])
)

val_equip1 = df_val[categorical_features].eq(0).all(axis=1)
val_equip2 = df_val[categorical_features].eq(1).all(axis=1)
condition_equip_different = ~val_equip1 & ~val_equip2 

# 조건들을 묶어서 필터링
val_condition = ( condition_receip | condition_production_qty | condition_equip_different )

val_abnormal = df_val[val_condition]
# abnormal로 제외하고 남은 데이터

val_filtered = df_val[~val_condition]
# 장비가 0 또는 1의 값으로 나누기 (label encoding으로 Equipment #1: 0 , Equipment #2: 1)

val_model1 = val_filtered[val_filtered[categorical_features].eq(0).all(axis=1)]
val_model2 = val_filtered[val_filtered[categorical_features].eq(1).all(axis=1)]

In [31]:
val_model1_train = val_model1.drop(columns = 'target')
val_model2_train = val_model2.drop(columns = 'target')

In [33]:
val_model1_predictions = model1_rf.predict(val_model1_train)
val_model2_predictions = model1_rf.predict(val_model2_train)

# 예측을 위한 데이터 인덱스
val_model1_index = val_model1.index
val_model2_index = val_model2.index

# 검증 데이터의 전체 예측을 위한 결과 결합
val_predictions = []

for idx in df_val.index:
    if idx in val_model1_index:
        val_predictions.append(val_model1_predictions[val_model1_index.get_loc(idx)])
    elif idx in val_model2_index:
        val_predictions.append(val_model2_predictions[val_model2_index.get_loc(idx)])
    else:
        val_predictions.append('AbNormal')


# 정확도 계산
val_accuracy = accuracy_score(y_val, val_predictions)

# F1 스코어 계산
val_f1_score = f1_score(y_val, val_predictions, pos_label="AbNormal")

# 결과 출력
print(f"검증 데이터 정확도: {val_accuracy:.4f}")
print(f"검증 데이터 F1 스코어: {val_f1_score:.4f}")

검증 데이터 정확도: 0.9340
검증 데이터 F1 스코어: 0.1558


In [34]:
# 혼동 행렬 생성
cm = confusion_matrix(y_val, val_predictions)

print(f"F1 스코어: {val_f1_score}")
print(f"혼동 행렬:\n{cm}")# 혼동 행렬 생성

F1 스코어: 0.15578947368421053
혼동 행렬:
[[   74   631]
 [  171 11276]]


## XGBoost

In [35]:
#pip install xgboost

### 모델 나누어서

In [36]:
# 데이터와 타겟 분리
X_model1 = df_model1.drop(columns='target')
y_model1 = df_model1['target']
X_model2 = df_model2.drop(columns='target')
y_model2 = df_model2['target']

y_model1_encoded = y_model1.replace({'Normal': 0, 'AbNormal': 1})
y_model2_encoded = y_model2.replace({'Normal': 0, 'AbNormal': 1})

In [37]:
from sklearn.model_selection import GridSearchCV
from xgboost import XGBClassifier

# 모델 훈련
model1 = XGBClassifier(random_state=RANDOM_STATE)
model1.fit(X_model1, y_model1_encoded)

model2 = XGBClassifier(random_state=RANDOM_STATE)
model2.fit(X_model2, y_model2_encoded)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=None, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=None, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=None, n_jobs=None,
              num_parallel_tree=None, random_state=42, ...)

In [38]:
param_grid = {
    'max_depth': [3, 5, 7],
    'eta': [0.01, 0.1, 0.3],
    'subsample': [0.6, 0.8, 1.0],
    'colsample_bytree': [0.6, 0.8, 1.0],
    'reg_alpha': [0, 0.1, 1],
    'reg_lambda': [0.5, 1, 2]
}

model1 = XGBClassifier(random_state=RANDOM_STATE)

model1_xgb_grid_search = GridSearchCV(estimator=model1, param_grid=param_grid, 
                           scoring='f1_weighted', cv=5, verbose=2, n_jobs=-1)

model1_xgb_grid_search.fit(X_model1, y_model1_encoded)

Fitting 5 folds for each of 729 candidates, totalling 3645 fits
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0, reg_lambda=0.5, subsample=0.8; total time=   0.3s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0, reg_lambda=0.5, subsample=1.0; total time=   0.2s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0, reg_lambda=1, subsample=0.8; total time=   0.2s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0, reg_lambda=1, subsample=1.0; total time=   0.2s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0, reg_lambda=2, subsample=0.8; total time=   0.2s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0, reg_lambda=2, subsample=1.0; total time=   0.3s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0.1, reg_lambda=0.5, subsample=0.8; total time=   0.3s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0.1, reg_lambda=1, subsample=0.6; total time=   0.3s
[CV] E

/Users/kkw/myvenv/lib/python3.11/site-packages/joblib/externals/loky/process_executor.py:752: UserWarning: A worker stopped while some jobs were given to the executor. This can be caused by a too short worker timeout or by a memory leak.
  warnings.warn(


[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0, reg_lambda=0.5, subsample=0.8; total time=   0.2s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0, reg_lambda=0.5, subsample=0.8; total time=   0.2s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0, reg_lambda=1, subsample=0.6; total time=   0.2s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0, reg_lambda=1, subsample=1.0; total time=   0.2s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0, reg_lambda=2, subsample=0.8; total time=   0.2s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0, reg_lambda=2, subsample=1.0; total time=   0.2s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0.1, reg_lambda=0.5, subsample=0.8; total time=   0.2s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0.1, reg_lambda=0.5, subsample=1.0; total time=   0.2s
[CV] END colsample_bytree=0.6, eta=0.01, max_depth=3, reg_alpha=0.1,

GridSearchCV(cv=5,
             estimator=XGBClassifier(base_score=None, booster=None,
                                     callbacks=None, colsample_bylevel=None,
                                     colsample_bynode=None,
                                     colsample_bytree=None, device=None,
                                     early_stopping_rounds=None,
                                     enable_categorical=False, eval_metric=None,
                                     feature_types=None, gamma=None,
                                     grow_policy=None, importance_type=None,
                                     interaction_constraints=None,
                                     learning_rate=None,...
                                     max_leaves=None, min_child_weight=None,
                                     missing=nan, monotone_constraints=None,
                                     multi_strategy=None, n_estimators=None,
                                     n_jobs=None, num_parallel_tree=None,
                                     random_state=42, ...),
             n_jobs=-1,
             param_grid={'colsample_bytree': [0.6, 0.8, 1.0],
                         'eta': [0.01, 0.1, 0.3], 'max_depth': [3, 5, 7],
                         'reg_alpha': [0, 0.1, 1], 'reg_lambda': [0.5, 1, 2],
                         'subsample': [0.6, 0.8, 1.0]},
             scoring='f1_weighted', verbose=2)

In [39]:
model2 = XGBClassifier(random_state=RANDOM_STATE)
                                
model2_xgb_grid_search = GridSearchCV(estimator=model2, param_grid=param_grid, 
                           scoring='f1_weighted', cv=5, verbose=2, n_jobs=-1)

model2_xgb_grid_search.fit(X_model2, y_model2_encoded)

Fitting 5 folds for each of 729 candidates, totalling 3645 fits
[CV] END colsample_bytree=1.0, eta=0.1, max_depth=5, reg_alpha=0.1, reg_lambda=2, subsample=0.8; total time=   0.4s
[CV] END colsample_bytree=1.0, eta=0.1, max_depth=5, reg_alpha=1, reg_lambda=0.5, subsample=1.0; total time=   0.3s
[CV] END colsample_bytree=1.0, eta=0.1, max_depth=5, reg_alpha=1, reg_lambda=1, subsample=0.6; total time=   0.4s
[CV] END colsample_bytree=1.0, eta=0.1, max_depth=5, reg_alpha=1, reg_lambda=1, subsample=1.0; total time=   0.3s
[CV] END colsample_bytree=1.0, eta=0.1, max_depth=5, reg_alpha=1, reg_lambda=2, subsample=0.8; total time=   0.4s
[CV] END colsample_bytree=1.0, eta=0.1, max_depth=5, reg_alpha=1, reg_lambda=2, subsample=1.0; total time=   0.4s
[CV] END colsample_bytree=1.0, eta=0.1, max_depth=7, reg_alpha=0, reg_lambda=0.5, subsample=0.8; total time=   0.5s
[CV] END colsample_bytree=1.0, eta=0.1, max_depth=7, reg_alpha=0, reg_lambda=1, subsample=0.6; total time=   0.5s
[CV] END colsample

/Users/kkw/myvenv/lib/python3.11/site-packages/joblib/externals/loky/process_executor.py:752: UserWarning: A worker stopped while some jobs were given to the executor. This can be caused by a too short worker timeout or by a memory leak.
  warnings.warn(


GridSearchCV(cv=5,
             estimator=XGBClassifier(base_score=None, booster=None,
                                     callbacks=None, colsample_bylevel=None,
                                     colsample_bynode=None,
                                     colsample_bytree=None, device=None,
                                     early_stopping_rounds=None,
                                     enable_categorical=False, eval_metric=None,
                                     feature_types=None, gamma=None,
                                     grow_policy=None, importance_type=None,
                                     interaction_constraints=None,
                                     learning_rate=None,...
                                     max_leaves=None, min_child_weight=None,
                                     missing=nan, monotone_constraints=None,
                                     multi_strategy=None, n_estimators=None,
                                     n_jobs=None, num_parallel_tree=None,
                                     random_state=42, ...),
             n_jobs=-1,
             param_grid={'colsample_bytree': [0.6, 0.8, 1.0],
                         'eta': [0.01, 0.1, 0.3], 'max_depth': [3, 5, 7],
                         'reg_alpha': [0, 0.1, 1], 'reg_lambda': [0.5, 1, 2],
                         'subsample': [0.6, 0.8, 1.0]},
             scoring='f1_weighted', verbose=2)

In [40]:
model1_xgb = XGBClassifier(**model1_xgb_grid_search.best_params_, random_state=RANDOM_STATE, class_weight='balanced')
model1_xgb.fit(X_model1, y_model1_encoded)
model2_xgb = XGBClassifier(**model2_xgb_grid_search.best_params_, random_state=RANDOM_STATE, class_weight='balanced')
model2_xgb.fit(X_model2, y_model2_encoded)

/Users/kkw/myvenv/lib/python3.11/site-packages/xgboost/core.py:160: UserWarning: [22:39:33] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "class_weight" } are not used.

  warnings.warn(smsg, UserWarning)
/Users/kkw/myvenv/lib/python3.11/site-packages/xgboost/core.py:160: UserWarning: [22:39:33] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "class_weight" } are not used.

  warnings.warn(smsg, UserWarning)


XGBClassifier(base_score=None, booster=None, callbacks=None,
              class_weight='balanced', colsample_bylevel=None,
              colsample_bynode=None, colsample_bytree=0.8, device=None,
              early_stopping_rounds=None, enable_categorical=False, eta=0.1,
              eval_metric=None, feature_types=None, gamma=None,
              grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=None, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=7, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=None, n_jobs=None, ...)

In [41]:
print("Best1 parameters found: ", model1_xgb_grid_search.best_params_)
print("Best1 parameters score: \n", model1_xgb_grid_search.best_score_)

print("Best1 parameters found: ", model2_xgb_grid_search.best_params_)
print("Best1 parameters score: \n", model2_xgb_grid_search.best_score_)

Best1 parameters found:  {'colsample_bytree': 1.0, 'eta': 0.3, 'max_depth': 5, 'reg_alpha': 0.1, 'reg_lambda': 0.5, 'subsample': 1.0}
Best1 parameters score: 
 0.8429933316191608
Best1 parameters found:  {'colsample_bytree': 0.8, 'eta': 0.1, 'max_depth': 7, 'reg_alpha': 0, 'reg_lambda': 0.5, 'subsample': 1.0}
Best1 parameters score: 
 0.8661940385046633


In [42]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, f1_score

y_val = df_val["target"]
y_val_encoded = y_val.replace({'Normal': 0, 'AbNormal': 1})

# 세 가지 조건: 열 간 값이 다르면 불량으로 분류
condition_receip = (
    (df_val['Receip No Collect Result_Dam'] != df_val['Receip No Collect Result_Fill1']) |
    (df_val['Receip No Collect Result_Dam'] != df_val['Receip No Collect Result_Fill2']) |
    (df_val['Receip No Collect Result_Fill1'] != df_val['Receip No Collect Result_Fill2'])
)

condition_production_qty = (
    (df_val['Production Qty Collect Result_Dam'] != df_val['Production Qty Collect Result_Fill1']) |
    (df_val['Production Qty Collect Result_Dam'] != df_val['Production Qty Collect Result_Fill2']) |
    (df_val['Production Qty Collect Result_Fill1'] != df_val['Production Qty Collect Result_Fill2'])
)

val_equip1 = df_val[categorical_features].eq(0).all(axis=1)
val_equip2 = df_val[categorical_features].eq(1).all(axis=1)
condition_equip_different = ~val_equip1 & ~val_equip2 

# 조건들을 묶어서 필터링
val_condition = ( condition_receip | condition_production_qty | condition_equip_different )

val_abnormal = df_val[val_condition]
# abnormal로 제외하고 남은 데이터

val_filtered = df_val[~val_condition]
# 장비가 0 또는 1의 값으로 나누기 (label encoding으로 Equipment #1: 0 , Equipment #2: 1)

val_model1 = val_filtered[val_filtered[categorical_features].eq(0).all(axis=1)]
val_model2 = val_filtered[val_filtered[categorical_features].eq(1).all(axis=1)]

val_model1_train = val_model1.drop(columns = 'target')
val_model2_train = val_model2.drop(columns = 'target')

In [43]:
val_model1_predictions = model1_xgb.predict(val_model1_train)
val_model2_predictions = model2_xgb.predict(val_model2_train)

# 예측을 위한 데이터 인덱스
val_model1_index = val_model1.index
val_model2_index = val_model2.index

# 검증 데이터의 전체 예측을 위한 결과 결합
val_predictions = []

for idx in df_val.index:
    if idx in val_model1_index:
        val_predictions.append(val_model1_predictions[val_model1_index.get_loc(idx)])
    elif idx in val_model2_index:
        val_predictions.append(val_model2_predictions[val_model2_index.get_loc(idx)])
    else:
        val_predictions.append(1)


# 정확도 계산
val_accuracy = accuracy_score(y_val_encoded, val_predictions)

# F1 스코어 계산
val_f1_score = f1_score(y_val_encoded, val_predictions, pos_label=1)

# 결과 출력
print(f"검증 데이터 정확도: {val_accuracy:.4f}")
print(f"검증 데이터 F1 스코어: {val_f1_score:.4f}")

검증 데이터 정확도: 0.9400
검증 데이터 F1 스코어: 0.1611


# SVC

In [44]:
from sklearn.model_selection import GridSearchCV
from sklearn.svm import SVC

model1_svm = SVC(kernel = 'rbf',random_state=RANDOM_STATE)

parameters = {'C': [0.1, 1, 10, 50, 100],
             'gamma':[0.001, 0.01, 0.1, 1]}

model1_svm_grid_search = GridSearchCV(model1_svm,
                      param_grid = parameters, cv = 5)

model1_svm_grid_search.fit(X_model1, y_model1)

[CV] END colsample_bytree=1.0, eta=0.3, max_depth=3, reg_alpha=0.1, reg_lambda=1, subsample=0.6; total time=   0.3s
[CV] END colsample_bytree=1.0, eta=0.3, max_depth=3, reg_alpha=0.1, reg_lambda=2, subsample=0.8; total time=   0.3s
[CV] END colsample_bytree=1.0, eta=0.3, max_depth=3, reg_alpha=0.1, reg_lambda=2, subsample=1.0; total time=   0.3s
[CV] END colsample_bytree=1.0, eta=0.3, max_depth=3, reg_alpha=1, reg_lambda=0.5, subsample=0.8; total time=   0.3s
[CV] END colsample_bytree=1.0, eta=0.3, max_depth=3, reg_alpha=1, reg_lambda=1, subsample=0.6; total time=   0.3s
[CV] END colsample_bytree=1.0, eta=0.3, max_depth=3, reg_alpha=1, reg_lambda=1, subsample=0.8; total time=   0.3s
[CV] END colsample_bytree=1.0, eta=0.3, max_depth=3, reg_alpha=1, reg_lambda=2, subsample=0.6; total time=   0.3s
[CV] END colsample_bytree=1.0, eta=0.3, max_depth=3, reg_alpha=1, reg_lambda=2, subsample=0.8; total time=   0.3s
[CV] END colsample_bytree=1.0, eta=0.3, max_depth=5, reg_alpha=0, reg_lambda=0.5

GridSearchCV(cv=5, estimator=SVC(random_state=42),
             param_grid={'C': [0.1, 1, 10, 50, 100],
                         'gamma': [0.001, 0.01, 0.1, 1]})

In [45]:
result1 = pd.DataFrame(model1_svm_grid_search.cv_results_['params'])
result1['mean_test_score'] = model1_svm_grid_search.cv_results_['mean_test_score']
result1.sort_values(by='mean_test_score', ascending=False)

C  gamma  mean_test_score
4     1.0  0.001         0.889064
0     0.1  0.001         0.887486
7     1.0  1.000         0.887486
15   50.0  1.000         0.887486
11   10.0  1.000         0.887486
1     0.1  0.010         0.887486
19  100.0  1.000         0.887486
6     1.0  0.100         0.887486
3     0.1  1.000         0.887486
2     0.1  0.100         0.887486
5     1.0  0.010         0.885118
14   50.0  0.100         0.878129
18  100.0  0.100         0.878129
10   10.0  0.100         0.878129
8    10.0  0.001         0.865840
9    10.0  0.010         0.841375
12   50.0  0.001         0.837317
13   50.0  0.010         0.836979
17  100.0  0.010         0.836077
16  100.0  0.001         0.825479

In [46]:
model2_svm = SVC(kernel = 'rbf',random_state=RANDOM_STATE)
model2_svm_grid_search = GridSearchCV(model2_svm,
                      param_grid = parameters, cv = 5)

model2_svm_grid_search.fit(X_model2, y_model2)

GridSearchCV(cv=5, estimator=SVC(random_state=42),
             param_grid={'C': [0.1, 1, 10, 50, 100],
                         'gamma': [0.001, 0.01, 0.1, 1]})

In [47]:
result2 = pd.DataFrame(model2_svm_grid_search.cv_results_['params'])
result2['mean_test_score'] = model2_svm_grid_search.cv_results_['mean_test_score']
result2.sort_values(by='mean_test_score', ascending=False)

C  gamma  mean_test_score
4     1.0  0.001         0.899014
5     1.0  0.010         0.898829
0     0.1  0.001         0.895853
18  100.0  0.100         0.893435
14   50.0  0.100         0.893435
10   10.0  0.100         0.893435
6     1.0  0.100         0.892133
7     1.0  1.000         0.891203
1     0.1  0.010         0.891203
11   10.0  1.000         0.891203
3     0.1  1.000         0.891203
15   50.0  1.000         0.891203
2     0.1  0.100         0.891203
19  100.0  1.000         0.891203
8    10.0  0.001         0.877440
9    10.0  0.010         0.858471
13   50.0  0.010         0.857541
17  100.0  0.010         0.857541
12   50.0  0.001         0.841924
16  100.0  0.001         0.830021

In [48]:
model1_svm = SVC(**model1_svm_grid_search.best_params_, kernel = 'rbf', random_state=RANDOM_STATE)
model1_svm.fit(X_model1, y_model1)
model2_svm = SVC(**model2_svm_grid_search.best_params_, kernel = 'rbf', random_state=RANDOM_STATE)
model2_svm.fit(X_model2, y_model2)

SVC(C=1, gamma=0.001, random_state=42)

In [49]:
val_model1_predictions = model1_svm.predict(val_model1_train)
val_model2_predictions = model2_svm.predict(val_model2_train)

# 예측을 위한 데이터 인덱스
val_model1_index = val_model1.index
val_model2_index = val_model2.index

# 검증 데이터의 전체 예측을 위한 결과 결합
val_predictions = []

for idx in df_val.index:
    if idx in val_model1_index:
        val_predictions.append(val_model1_predictions[val_model1_index.get_loc(idx)])
    elif idx in val_model2_index:
        val_predictions.append(val_model2_predictions[val_model2_index.get_loc(idx)])
    else:
        val_predictions.append('AbNormal')


# 정확도 계산
val_accuracy = accuracy_score(y_val, val_predictions)

# F1 스코어 계산
val_f1_score = f1_score(y_val, val_predictions, pos_label='AbNormal')

# 결과 출력
print(f"검증 데이터 정확도: {val_accuracy:.4f}")
print(f"검증 데이터 F1 스코어: {val_f1_score:.4f}")

검증 데이터 정확도: 0.9442
검증 데이터 F1 스코어: 0.1567


## LGBM

In [50]:
# # lgbm오류? -> 

# from lightgbm import LGBMClassifier
# from sklearn.model_selection import GridSearchCV

# # LightGBM 모델 정의
# model1_lgbm = LGBMClassifier(random_state=RANDOM_STATE)
# model2_lgbm = LGBMClassifier(random_state=RANDOM_STATE)

# # 하이퍼파라미터 그리드 설정
# param_grid = {
#     'learning_rate': [0.01, 0.05, 0.1],
#     'n_estimators': [100, 200, 500],
#     'max_depth': [ 10, 15],
#     'num_leaves': [31, 50, 100],
#     'subsample': [0.6, 0.8, 1.0],
#     'colsample_bytree': [0.8, 1.0]
# }

# model1_lgbm_grid_search = GridSearchCV(estimator=model1_lgbm, param_grid=param_grid,
#                                        cv=5, verbose=1, n_jobs = -1)

# # 모델 학습
# model1_lgbm_grid_search.fit(X_model1, y_model1)

Fitting 5 folds for each of 486 candidates, totalling 2430 fits
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 6297, number of negative: 799
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.014022 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3350
[LightGBM] [Info] Number of data points in the train set: 7096, number of used features: 124
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.887401 -> initscore=2.064468
[LightGBM] [Info] Start training from score 2.064468
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 6298, number of negative: 798
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002088 seconds.
You can set `force_row_wise=true` to remove the ove

KeyboardInterrupt: 

In [ ]:
# model2_lgbm_grid_search = GridSearchCV(estimator=model2_lgbm, param_grid=param_grid,
#                                        cv=5, verbose=1, n_jobs = -1)

# # 모델 학습
# model2_lgbm_grid_search.fit(X_model2, y_model2)

In [ ]:
# print(model1_lgbm_grid_search.best_params_)
# print(model1_lgbm_grid_search.best_score_)

# print(model2_lgbm_grid_search.best_params_)
# print(model2_lgbm_grid_search.best_score_)

In [32]:
model1_lgbm_grid_search_best = {
    'colsample_bytree': 0.8, 'learning_rate': 0.01, 'max_depth': 10, 'n_estimators': 200, 'num_leaves': 50, 'subsample': 0.6
    }
model2_lgbm_grid_search_best = {'colsample_bytree': 0.8, 'learning_rate': 0.1, 'max_depth': -1, 'n_estimators': 500, 'num_leaves': 50, 'subsample': 0.6}

# 모델 정의 시 random_state 설정
model1_lgbm = LGBMClassifier(
    **model1_lgbm_grid_search_best,
    random_state=RANDOM_STATE, 
    class_weight='balanced'
)

model2_lgbm = LGBMClassifier(
    **model2_lgbm_grid_search_best,
    random_state=RANDOM_STATE, 
    class_weight='balanced'
)

# fit 메서드 호출 시 random_state 인자는 필요 없음
model1_lgbm.fit(X_model1, y_model1)
model2_lgbm.fit(X_model2, y_model2)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 7872, number of negative: 998
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001468 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3391
[LightGBM] [Info] Number of data points in the train set: 8870, number of used features: 126
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Info] Start training from score 0.000000
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 4792, number of negative: 585
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001322 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=

LGBMClassifier(class_weight='balanced', colsample_bytree=0.8, n_estimators=500,
               num_leaves=50, random_state=42, subsample=0.6)

In [33]:
val_model1_predictions = model1_lgbm.predict(val_model1_train)
val_model2_predictions = model2_lgbm.predict(val_model2_train)

# 예측을 위한 데이터 인덱스
val_model1_index = val_model1.index
val_model2_index = val_model2.index

# 검증 데이터의 전체 예측을 위한 결과 결합
val_predictions = []

for idx in df_val.index:
    if idx in val_model1_index:
        val_predictions.append(val_model1_predictions[val_model1_index.get_loc(idx)])
    elif idx in val_model2_index:
        val_predictions.append(val_model2_predictions[val_model2_index.get_loc(idx)])
    else:
        val_predictions.append('AbNormal')


# 정확도 계산
val_accuracy = accuracy_score(y_val, val_predictions)

# F1 스코어 계산
val_f1_score = f1_score(y_val, val_predictions, pos_label='AbNormal')

# 결과 출력
print(f"검증 데이터 정확도: {val_accuracy:.4f}")
print(f"검증 데이터 F1 스코어: {val_f1_score:.4f}")

검증 데이터 정확도: 0.7717
검증 데이터 F1 스코어: 0.1729


In [34]:
# 혼동 행렬 생성
cm = confusion_matrix(y_val, val_predictions)

print(f"F1 스코어: {val_f1_score}")
print(f"혼동 행렬:\n{cm}")# 혼동 행렬 생성

F1 스코어: 0.172927847346452
혼동 행렬:
[[ 290  415]
 [2359 9088]]


# 모델1

In [25]:
from sklearn.ensemble import RandomForestClassifier, VotingClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report

scale_pos_weight = len(y_model1[y_model1 == 'AbNormal']) / len(y_model1[y_model1 == 'Normal'])

model1_rf = RandomForestClassifier(**model1_rf_grid_search.best_params_,random_state=RANDOM_STATE,class_weight='balanced')
model1_xgb = XGBClassifier(**model1_xgb_grid_search.best_params_,random_state=RANDOM_STATE,class_weight='balanced')
model1_svm = SVC(**model1_svm_grid_search.best_params_, probability=True,kernel = 'rbf', random_state=RANDOM_STATE)
model1_lgbm = LGBMClassifier(**model1_lgbm_grid_search_best,class_weight='balanced',random_state=RANDOM_STATE)

# 앙상블 모델 정의 (투표 기반)
model1_voting = VotingClassifier(
    estimators=[('rf', model1_rf), ('xgb', model1_xgb), ('svm', model1_svm), ('lgbm', model1_lgbm)],
    voting='soft'
)

# 모델 학습
model1_voting.fit(X_model1, y_model1)

NameError: name 'model1_rf_grid_search' is not defined

# 모델2

In [77]:
scale_pos_weight = len(y_model2[y_model2 == 'AbNormal']) / len(y_model2[y_model2 == 'Normal'])
RANDOM_STATE = 42

model2_rf = RandomForestClassifier(**model2_rf_grid_search.best_params_,random_state=RANDOM_STATE,class_weight='balanced')
model2_xgb = XGBClassifier(**model2_xgb_grid_search.best_params_,random_state=RANDOM_STATE,class_weight='balanced')
model2_svm = SVC(**model2_svm_grid_search.best_params_,probability=True, kernel = 'rbf', random_state=RANDOM_STATE)
model2_lgbm = LGBMClassifier(**model1_lgbm_grid_search_best,class_weight='balanced',random_state=RANDOM_STATE)

# 앙상블 모델 정의 (투표 기반)
model2_voting = VotingClassifier(
    estimators=[('rf', model2_rf), ('xgb', model2_xgb), ('svm', model2_svm), ('lgbm', model2_lgbm)],
    voting='soft'
)

# 모델 학습
model2_voting.fit(X_model2, y_model2)

/Users/kkw/myvenv/lib/python3.11/site-packages/xgboost/core.py:160: UserWarning: [23:38:24] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:742: 
Parameters: { "class_weight" } are not used.

  warnings.warn(smsg, UserWarning)


[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Number of positive: 4792, number of negative: 585
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001512 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3183
[LightGBM] [Info] Number of data points in the train set: 5377, number of used features: 123
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=-0.000000
[LightGBM] [Info] Start training from score -0.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best g

VotingClassifier(estimators=[('rf',
                              RandomForestClassifier(class_weight='balanced',
                                                     max_depth=30,
                                                     min_samples_split=10,
                                                     random_state=42)),
                             ('xgb',
                              XGBClassifier(base_score=None, booster=None,
                                            callbacks=None,
                                            class_weight='balanced',
                                            colsample_bylevel=None,
                                            colsample_bynode=None,
                                            colsample_bytree=0.8, device=None,
                                            early_stopping_rounds=None,
                                            enable_categorical=Fal...
                                            min_child_weight=None, missing=nan,
                                            monotone_constraints=None,
                                            multi_strategy=None,
                                            n_estimators=None, n_jobs=None, ...)),
                             ('svm',
                              SVC(C=1, gamma=0.001, probability=True,
                                  random_state=42)),
                             ('lgbm',
                              LGBMClassifier(class_weight='balanced',
                                             colsample_bytree=0.8,
                                             learning_rate=0.01, max_depth=10,
                                             n_estimators=200, num_leaves=50,
                                             random_state=42, subsample=0.6))],
                 voting='soft')

In [78]:
from sklearn.metrics import accuracy_score, f1_score

y_val = df_val["target"]

# 세 가지 조건: 열 간 값이 다르면 불량으로 분류
condition_receip = (
    (df_val['Receip No Collect Result_Dam'] != df_val['Receip No Collect Result_Fill1']) |
    (df_val['Receip No Collect Result_Dam'] != df_val['Receip No Collect Result_Fill2']) |
    (df_val['Receip No Collect Result_Fill1'] != df_val['Receip No Collect Result_Fill2'])
)

condition_production_qty = (
    (df_val['Production Qty Collect Result_Dam'] != df_val['Production Qty Collect Result_Fill1']) |
    (df_val['Production Qty Collect Result_Dam'] != df_val['Production Qty Collect Result_Fill2']) |
    (df_val['Production Qty Collect Result_Fill1'] != df_val['Production Qty Collect Result_Fill2'])
)

val_equip1 = df_val[categorical_features].eq(0).all(axis=1)
val_equip2 = df_val[categorical_features].eq(1).all(axis=1)
condition_equip_different = ~val_equip1 & ~val_equip2 

# 조건들을 묶어서 필터링
val_condition = ( condition_receip | condition_production_qty | condition_equip_different )

val_abnormal = df_val[val_condition]
# abnormal로 제외하고 남은 데이터

val_filtered = df_val[~val_condition]
# 장비가 0 또는 1의 값으로 나누기 (label encoding으로 Equipment #1: 0 , Equipment #2: 1)

val_model1 = val_filtered[val_filtered[categorical_features].eq(0).all(axis=1)]
val_model2 = val_filtered[val_filtered[categorical_features].eq(1).all(axis=1)]

In [79]:
val_model1_predictions = model1_voting.predict(val_model1_train)
val_model2_predictions = model2_voting.predict(val_model2_train)

# 예측을 위한 데이터 인덱스
val_model1_index = val_model1.index
val_model2_index = val_model2.index

# 검증 데이터의 전체 예측을 위한 결과 결합
val_predictions = []

for idx in df_val.index:
    if idx in val_model1_index:
        val_predictions.append(val_model1_predictions[val_model1_index.get_loc(idx)])
    elif idx in val_model2_index:
        val_predictions.append(val_model2_predictions[val_model2_index.get_loc(idx)])
    else:
        val_predictions.append('AbNormal')


# 정확도 계산
val_accuracy = accuracy_score(y_val, val_predictions)

# F1 스코어 계산
val_f1_score = f1_score(y_val, val_predictions, pos_label='AbNormal')

# 결과 출력
print(f"검증 데이터 정확도: {val_accuracy:.4f}")
print(f"검증 데이터 F1 스코어: {val_f1_score:.4f}")

검증 데이터 정확도: 0.9434
검증 데이터 F1 스코어: 0.1589


In [80]:
# 혼동 행렬 생성
cm = confusion_matrix(y_val, val_predictions)

print(f"F1 스코어: {val_f1_score}")
print(f"혼동 행렬:\n{cm}")# 혼동 행렬 생성

F1 스코어: 0.15892420537897312
혼동 행렬:
[[   65   640]
 [   48 11399]]


# 4. 제출하기

### 테스트 데이터 예측


테스트 데이터 불러오기


In [81]:
test_data = pd.read_csv(os.path.join(ROOT_DIR, "test.csv"))
test_data

Set ID Wip Line_Dam Process Desc._Dam  \
0      0001be084fbc4aaa9d921f39e595961b      IVI-OB6     Dam Dispenser   
1      0005bbd180064abd99e63f9ed3e1ac80      IVI-OB6     Dam Dispenser   
2      000948934c4140d883d670adcb609584      IVI-OB6     Dam Dispenser   
3      000a6bfd02874c6296dc7b2e9c5678a7      IVI-OB6     Dam Dispenser   
4      0018e78ce91343678716e2ea27a51c95      IVI-OB6     Dam Dispenser   
...                                 ...          ...               ...   
17356  ffea508b59934d689b540f95eb3fa730      IVI-OB6     Dam Dispenser   
17357  ffed8923c8a448a98afc641b770be153      IVI-OB6     Dam Dispenser   
17358  fff1e73734da40adbe805359b3efb462      IVI-OB6     Dam Dispenser   
17359  fff8e38bdd09470baf95f71e92075dec      IVI-OB6     Dam Dispenser   
17360  fffa83e0a13d4c2db4fd8bf905b517d4      IVI-OB6     Dam Dispenser   

          Equipment_Dam Model.Suffix_Dam Workorder_Dam  Insp. Seq No._Dam  \
0      Dam dispenser #2      AJX75334501    3J1XF767-1                  1   
1      Dam dispenser #2      AJX75334501    4B1XD472-2                  1   
2      Dam dispenser #1      AJX75334501    3H1XE355-1                  1   
3      Dam dispenser #2      AJX75334501    3L1XA128-1                  1   
4      Dam dispenser #1      AJX75334501    4A1XA639-1                  1   
...                 ...              ...           ...                ...   
17356  Dam dispenser #2      AJX75334501    3K1XB597-1                  1   
17357  Dam dispenser #2      AJX75334501    4A1XB974-1                  1   
17358  Dam dispenser #1      AJX75334501    3L1XA998-1                  1   
17359  Dam dispenser #1      AJX75334501    3F1XC376-1                  1   
17360  Dam dispenser #1      AJX75334501    3J1XC756-1                  1   

      Insp Judge Code_Dam  CURE END POSITION X Collect Result_Dam  \
0                      OK                                  1000.0   
1                      OK                                  1000.0   
2                      OK                                   240.0   
3                      OK                                  1000.0   
4                      OK                                   240.0   
...                   ...                                     ...   
17356                  OK                                  1000.0   
17357                  OK                                  1000.0   
17358                  OK                                   240.0   
17359                  OK                                   240.0   
17360                  OK                                   240.0   

       CURE END POSITION X Unit Time_Dam  ...  \
0                                    NaN  ...   
1                                    NaN  ...   
2                                    NaN  ...   
3                                    NaN  ...   
4                                    NaN  ...   
...                                  ...  ...   
17356                                NaN  ...   
17357                                NaN  ...   
17358                                NaN  ...   
17359                                NaN  ...   
17360                                NaN  ...   

       Production Qty Collect Result_Fill2  Production Qty Unit Time_Fill2  \
0                                      195                             NaN   
1                                       14                             NaN   
2                                       98                             NaN   
3                                       14                             NaN   
4                                        1                             NaN   
...                                    ...                             ...   
17356                                   14                             NaN   
17357                                   12                             NaN   
17358                                    4                             NaN   
17359                

In [82]:
# Drop columns with more than half of the values missing
drop_cols = []
for column in test_data.columns:
    if (test_data[column].notnull().sum() // 2) < test_data[
        column
    ].isnull().sum():
        drop_cols.append(column)
test_data = test_data.drop(drop_cols, axis=1)

test_data

Set ID Wip Line_Dam Process Desc._Dam  \
0      0001be084fbc4aaa9d921f39e595961b      IVI-OB6     Dam Dispenser   
1      0005bbd180064abd99e63f9ed3e1ac80      IVI-OB6     Dam Dispenser   
2      000948934c4140d883d670adcb609584      IVI-OB6     Dam Dispenser   
3      000a6bfd02874c6296dc7b2e9c5678a7      IVI-OB6     Dam Dispenser   
4      0018e78ce91343678716e2ea27a51c95      IVI-OB6     Dam Dispenser   
...                                 ...          ...               ...   
17356  ffea508b59934d689b540f95eb3fa730      IVI-OB6     Dam Dispenser   
17357  ffed8923c8a448a98afc641b770be153      IVI-OB6     Dam Dispenser   
17358  fff1e73734da40adbe805359b3efb462      IVI-OB6     Dam Dispenser   
17359  fff8e38bdd09470baf95f71e92075dec      IVI-OB6     Dam Dispenser   
17360  fffa83e0a13d4c2db4fd8bf905b517d4      IVI-OB6     Dam Dispenser   

          Equipment_Dam Model.Suffix_Dam Workorder_Dam  Insp. Seq No._Dam  \
0      Dam dispenser #2      AJX75334501    3J1XF767-1                  1   
1      Dam dispenser #2      AJX75334501    4B1XD472-2                  1   
2      Dam dispenser #1      AJX75334501    3H1XE355-1                  1   
3      Dam dispenser #2      AJX75334501    3L1XA128-1                  1   
4      Dam dispenser #1      AJX75334501    4A1XA639-1                  1   
...                 ...              ...           ...                ...   
17356  Dam dispenser #2      AJX75334501    3K1XB597-1                  1   
17357  Dam dispenser #2      AJX75334501    4A1XB974-1                  1   
17358  Dam dispenser #1      AJX75334501    3L1XA998-1                  1   
17359  Dam dispenser #1      AJX75334501    3F1XC376-1                  1   
17360  Dam dispenser #1      AJX75334501    3J1XC756-1                  1   

      Insp Judge Code_Dam  CURE END POSITION X Collect Result_Dam  \
0                      OK                                  1000.0   
1                      OK                                  1000.0   
2                      OK                                   240.0   
3                      OK                                  1000.0   
4                      OK                                   240.0   
...                   ...                                     ...   
17356                  OK                                  1000.0   
17357                  OK                                  1000.0   
17358                  OK                                   240.0   
17359                  OK                                   240.0   
17360                  OK                                   240.0   

       CURE END POSITION Z Collect Result_Dam  ...  \
0                                        12.5  ...   
1                                        12.5  ...   
2                                         2.5  ...   
3                                        12.5  ...   
4                                         2.5  ...   
...                                       ...  ...   
17356                                    12.5  ...   
17357                                    12.5  ...   
17358                                     2.5  ...   
17359                                     2.5  ...   
17360                                     2.5  ...   

       Head Clean Position Y Collect Result_Fill2  \
0                                              50   
1                                             119   
2                                              50   
3                                             119   
4                                             119   
...                                           ...   
17356                                         119   
17357                                         119   
17358                                         119   
17359                                          50   
17360                                          50   

       Head Clean Position Z Collect Result_Fill2  \
0                                            91.8  

In [83]:
# 각 열의 NaN 값 개수 계산
nan_counts = test_data.isnull().sum()

# NaN 값이 있는 열들만 필터링
nan_columns = nan_counts[nan_counts > 0]

nan_columns

HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam      5468
HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1    5468
HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill2    5468
dtype: int64

In [84]:
# 각 열의 NaN 값이 있는 행을 표시
nan_dam = test_data['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam'].isnull()
nan_fill1 = test_data['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1'].isnull()
nan_fill2 = test_data['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill2'].isnull()

# 세 열의 NaN 값이 모두 같은 행에서 발생했는지 확인
nan_same_rows = nan_dam & nan_fill1 & nan_fill2

# NaN 값이 동일한 행의 개수 확인
num_same_nan_rows = nan_same_rows.sum()

# 결과 출력
print(f"세 열에서 NaN 값이 동일한 행의 개수: {num_same_nan_rows}")
print(f"세 열에서 NaN 값이 동일한 행:\n{test_data[nan_same_rows]}")

세 열에서 NaN 값이 동일한 행의 개수: 5468
세 열에서 NaN 값이 동일한 행:
                                 Set ID Wip Line_Dam Process Desc._Dam  \
3      000a6bfd02874c6296dc7b2e9c5678a7      IVI-OB6     Dam Dispenser   
8      00297b6c93e44d49ac534758a23dc74e      IVI-OB6     Dam Dispenser   
9      002d904240d84b188d410d16383a9c3a      IVI-OB6     Dam Dispenser   
10     002fdfad651c4a98b6f0c4046976aac3      IVI-OB6     Dam Dispenser   
13     0039b02541014d678d5b0e5a3cb3797a      IVI-OB6     Dam Dispenser   
...                                 ...          ...               ...   
17349  ffd71ad9aac547a4a367d538c6e3ee30      IVI-OB6     Dam Dispenser   
17354  ffe5c71ef7b045868d177023be7f364b      IVI-OB6     Dam Dispenser   
17355  ffe77be574b24429b1bf6a69b5c2c2ef      IVI-OB6     Dam Dispenser   
17356  ffea508b59934d689b540f95eb3fa730      IVI-OB6     Dam Dispenser   
17358  fff1e73734da40adbe805359b3efb462      IVI-OB6     Dam Dispenser   

          Equipment_Dam Model.Suffix_Dam Workorder_Dam  Insp. 

In [85]:
# 삭제할 열 리스트
columns_to_drop = [
        'Model.Suffix_Fill1', 'Model.Suffix_Fill2', 'Model.Suffix_AutoClave', 
        'Workorder_Fill1', 'Workorder_Fill2', 'Workorder_AutoClave'
]

# 열 삭제
test_data = test_data.drop(columns=columns_to_drop)

# 열 이름 변경
test_data = test_data.rename(columns={
    'Model.Suffix_Dam': 'Model.Suffix',
    'Workorder_Dam': 'Workorder'
})

test_data

Set ID Wip Line_Dam Process Desc._Dam  \
0      0001be084fbc4aaa9d921f39e595961b      IVI-OB6     Dam Dispenser   
1      0005bbd180064abd99e63f9ed3e1ac80      IVI-OB6     Dam Dispenser   
2      000948934c4140d883d670adcb609584      IVI-OB6     Dam Dispenser   
3      000a6bfd02874c6296dc7b2e9c5678a7      IVI-OB6     Dam Dispenser   
4      0018e78ce91343678716e2ea27a51c95      IVI-OB6     Dam Dispenser   
...                                 ...          ...               ...   
17356  ffea508b59934d689b540f95eb3fa730      IVI-OB6     Dam Dispenser   
17357  ffed8923c8a448a98afc641b770be153      IVI-OB6     Dam Dispenser   
17358  fff1e73734da40adbe805359b3efb462      IVI-OB6     Dam Dispenser   
17359  fff8e38bdd09470baf95f71e92075dec      IVI-OB6     Dam Dispenser   
17360  fffa83e0a13d4c2db4fd8bf905b517d4      IVI-OB6     Dam Dispenser   

          Equipment_Dam Model.Suffix   Workorder  Insp. Seq No._Dam  \
0      Dam dispenser #2  AJX75334501  3J1XF767-1                  1   
1      Dam dispenser #2  AJX75334501  4B1XD472-2                  1   
2      Dam dispenser #1  AJX75334501  3H1XE355-1                  1   
3      Dam dispenser #2  AJX75334501  3L1XA128-1                  1   
4      Dam dispenser #1  AJX75334501  4A1XA639-1                  1   
...                 ...          ...         ...                ...   
17356  Dam dispenser #2  AJX75334501  3K1XB597-1                  1   
17357  Dam dispenser #2  AJX75334501  4A1XB974-1                  1   
17358  Dam dispenser #1  AJX75334501  3L1XA998-1                  1   
17359  Dam dispenser #1  AJX75334501  3F1XC376-1                  1   
17360  Dam dispenser #1  AJX75334501  3J1XC756-1                  1   

      Insp Judge Code_Dam  CURE END POSITION X Collect Result_Dam  \
0                      OK                                  1000.0   
1                      OK                                  1000.0   
2                      OK                                   240.0   
3                      OK                                  1000.0   
4                      OK                                   240.0   
...                   ...                                     ...   
17356                  OK                                  1000.0   
17357                  OK                                  1000.0   
17358                  OK                                   240.0   
17359                  OK                                   240.0   
17360                  OK                                   240.0   

       CURE END POSITION Z Collect Result_Dam  ...  \
0                                        12.5  ...   
1                                        12.5  ...   
2                                         2.5  ...   
3                                        12.5  ...   
4                                         2.5  ...   
...                                       ...  ...   
17356                                    12.5  ...   
17357                                    12.5  ...   
17358                                     2.5  ...   
17359                                     2.5  ...   
17360                                     2.5  ...   

       Head Clean Position Y Collect Result_Fill2  \
0                                              50   
1                                             119   
2                                              50   
3                                             119   
4                                             119   
...                                           ...   
17356                                         119   
17357                                         119   
17358                                         119   
17359                                          50   
17360                                          50   

       Head Clean Position Z Collect Result_Fill2  \
0                                            91.8   
1                                            50.0   
2                

In [86]:
# 모든 행이 동일한 값을 가지는 열을 찾고, 그 값을 함께 저장
constant_columns = {col: test_data[col].iloc[0] for col in test_data.columns if test_data[col].nunique() == 1}

# 데이터 프레임에서 해당 열 삭제
test_data = test_data.drop(columns=constant_columns.keys())

# 삭제된 열의 개수 출력
print(f"삭제된 열의 개수: {len(constant_columns)}")

# 삭제된 열과 그 값을 한 줄에 하나씩 출력
print("삭제된 열과 값:")
for col, value in constant_columns.items():
    print(f"{col}: {value}")

test_data

삭제된 열의 개수: 35
삭제된 열과 값:
Wip Line_Dam: IVI-OB6
Process Desc._Dam: Dam Dispenser
Insp. Seq No._Dam: 1
Insp Judge Code_Dam: OK
CURE STANDBY POSITION X Collect Result_Dam: 1150
CURE STANDBY POSITION Z Collect Result_Dam: 33.5
CURE STANDBY POSITION Θ Collect Result_Dam: 0
CURE START POSITION Z Collect Result_Dam: 33.5
Wip Line_AutoClave: IVI-OB6
Process Desc._AutoClave: Auto Clave Out
Equipment_AutoClave: Auto Clave Out
Insp. Seq No._AutoClave: 1
Insp Judge Code_AutoClave: OK
1st Pressure Judge Value_AutoClave: OK
2nd Pressure Judge Value_AutoClave: OK
3rd Pressure Judge Value_AutoClave: OK
Wip Line_Fill1: IVI-OB6
Process Desc._Fill1: Fill1 Dispenser
Insp. Seq No._Fill1: 1
Insp Judge Code_Fill1: OK
Wip Line_Fill2: IVI-OB6
Process Desc._Fill2: Fill2 Dispenser
Insp. Seq No._Fill2: 1
Insp Judge Code_Fill2: OK
CURE END POSITION Θ Collect Result_Fill2: -90
CURE STANDBY POSITION X Collect Result_Fill2: 1020
CURE STANDBY POSITION Θ Collect Result_Fill2: 0
CURE START POSITION Θ Collect Result_Fill2

Set ID     Equipment_Dam Model.Suffix  \
0      0001be084fbc4aaa9d921f39e595961b  Dam dispenser #2  AJX75334501   
1      0005bbd180064abd99e63f9ed3e1ac80  Dam dispenser #2  AJX75334501   
2      000948934c4140d883d670adcb609584  Dam dispenser #1  AJX75334501   
3      000a6bfd02874c6296dc7b2e9c5678a7  Dam dispenser #2  AJX75334501   
4      0018e78ce91343678716e2ea27a51c95  Dam dispenser #1  AJX75334501   
...                                 ...               ...          ...   
17356  ffea508b59934d689b540f95eb3fa730  Dam dispenser #2  AJX75334501   
17357  ffed8923c8a448a98afc641b770be153  Dam dispenser #2  AJX75334501   
17358  fff1e73734da40adbe805359b3efb462  Dam dispenser #1  AJX75334501   
17359  fff8e38bdd09470baf95f71e92075dec  Dam dispenser #1  AJX75334501   
17360  fffa83e0a13d4c2db4fd8bf905b517d4  Dam dispenser #1  AJX75334501   

        Workorder  CURE END POSITION X Collect Result_Dam  \
0      3J1XF767-1                                  1000.0   
1      4B1XD472-2                                  1000.0   
2      3H1XE355-1                                   240.0   
3      3L1XA128-1                                  1000.0   
4      4A1XA639-1                                   240.0   
...           ...                                     ...   
17356  3K1XB597-1                                  1000.0   
17357  4A1XB974-1                                  1000.0   
17358  3L1XA998-1                                   240.0   
17359  3F1XC376-1                                   240.0   
17360  3J1XC756-1                                   240.0   

       CURE END POSITION Z Collect Result_Dam  \
0                                        12.5   
1                                        12.5   
2                                         2.5   
3                                        12.5   
4                                         2.5   
...                                       ...   
17356                                    12.5   
17357                                    12.5   
17358                                     2.5   
17359                                     2.5   
17360                                     2.5   

       CURE END POSITION Θ Collect Result_Dam  CURE SPEED Collect Result_Dam  \
0                                          90                             70   
1                                          90                             70   
2                                         -90                             70   
3                                          90                             70   
4                                         -90                             70   
...                                       ...                            ...   
17356                                      90                             70   
17357                                      90                             70   
17358                                     -90                             70   
17359                                     -90                             70   
17360                                     -90                             70   

       CURE START POSITION X Collect Result_Dam  \
0                                           280   
1                                           280   
2                                          1030   
3                                           280   
4                                          1030   
...                                         ...   
17356                                       280   
17357                                       280   
17358                                      1030   
17359                                      1030   
17360                                      1030   

       CURE START POSITION Θ Collect Result_Dam  ...  \
0                                            90  ...   
1                                            90  ...   
2                                           -90  ...   
3                       

In [87]:
# 변환할 열들의 리스트
columns_to_convert = [
    'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam',
    'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1',
    'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill2']

# 각 열을 float로 변환
for col in columns_to_convert:
    test_data[col] = pd.to_numeric(test_data[col], errors='coerce')

test_data[columns_to_convert].dtypes

HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam      float64
HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1    float64
HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill2    float64
dtype: object

In [88]:
# # 제거할 열 리스트
columns_to_drop = ['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam', 
                   'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1', 
                   'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill2']
#   'WorkMode Collect Result_Dam', 'WorkMode Collect Result_Fill1', 'WorkMode Collect Result_Fill2'
# # 지정한 열 제거
test_data = test_data.drop(columns=columns_to_drop)

In [89]:
from sklearn.preprocessing import LabelEncoder
from sklearn.compose import make_column_transformer
from sklearn.preprocessing import OrdinalEncoder
from sklearn.pipeline import Pipeline

# 범주형 열을 선택하여 인코딩 수행
categorical_features = ['Equipment_Dam', 'Equipment_Fill1', 'Equipment_Fill2', 'Chamber Temp. Judge Value_AutoClave', 'Model.Suffix', 'Workorder']

# OrdinalEncoder 인스턴스 생성
encoder = OrdinalEncoder()

# 범주형 열에 대해서만 인코딩 수행
test_data[categorical_features] = encoder.fit_transform(test_data[categorical_features])

# 인코딩된 데이터프레임 확인
test_data

Set ID  Equipment_Dam  Model.Suffix  \
0      0001be084fbc4aaa9d921f39e595961b            1.0           0.0   
1      0005bbd180064abd99e63f9ed3e1ac80            1.0           0.0   
2      000948934c4140d883d670adcb609584            0.0           0.0   
3      000a6bfd02874c6296dc7b2e9c5678a7            1.0           0.0   
4      0018e78ce91343678716e2ea27a51c95            0.0           0.0   
...                                 ...            ...           ...   
17356  ffea508b59934d689b540f95eb3fa730            1.0           0.0   
17357  ffed8923c8a448a98afc641b770be153            1.0           0.0   
17358  fff1e73734da40adbe805359b3efb462            0.0           0.0   
17359  fff8e38bdd09470baf95f71e92075dec            0.0           0.0   
17360  fffa83e0a13d4c2db4fd8bf905b517d4            0.0           0.0   

       Workorder  CURE END POSITION X Collect Result_Dam  \
0          240.0                                  1000.0   
1          509.0                                  1000.0   
2          128.0                                   240.0   
3          306.0                                  1000.0   
4          415.0                                   240.0   
...          ...                                     ...   
17356      277.0                                  1000.0   
17357      439.0                                  1000.0   
17358      314.0                                   240.0   
17359        8.0                                   240.0   
17360      211.0                                   240.0   

       CURE END POSITION Z Collect Result_Dam  \
0                                        12.5   
1                                        12.5   
2                                         2.5   
3                                        12.5   
4                                         2.5   
...                                       ...   
17356                                    12.5   
17357                                    12.5   
17358                                     2.5   
17359                                     2.5   
17360                                     2.5   

       CURE END POSITION Θ Collect Result_Dam  CURE SPEED Collect Result_Dam  \
0                                          90                             70   
1                                          90                             70   
2                                         -90                             70   
3                                          90                             70   
4                                         -90                             70   
...                                       ...                            ...   
17356                                      90                             70   
17357                                      90                             70   
17358                                     -90                             70   
17359                                     -90                             70   
17360                                     -90                             70   

       CURE START POSITION X Collect Result_Dam  \
0                                           280   
1                                           280   
2                                          1030   
3                                           280   
4                                          1030   
...                                         ...   
17356                                       280   
17357                                       280   
17358                                      1030   
17359                                      1030   
17360                                      1030   

       CURE START POSITION Θ Collect Result_Dam  ...  \
0                                            90  ...   
1                                            90  ...   
2                                           -90  ...   
3                                            90  ...   
4   

In [90]:
categorical_features = ['Equipment_Dam', 'Equipment_Fill1', 'Equipment_Fill2']

# 세 가지 조건: 열 간 값이 다르면 불량으로 분류
condition_receip = (
    (test_data['Receip No Collect Result_Dam'] != test_data['Receip No Collect Result_Fill1']) |
    (test_data['Receip No Collect Result_Dam'] != test_data['Receip No Collect Result_Fill2']) |
    (test_data['Receip No Collect Result_Fill1'] != test_data['Receip No Collect Result_Fill2'])
)

condition_production_qty = (
    (test_data['Production Qty Collect Result_Dam'] != test_data['Production Qty Collect Result_Fill1']) |
    (test_data['Production Qty Collect Result_Dam'] != test_data['Production Qty Collect Result_Fill2']) |
    (test_data['Production Qty Collect Result_Fill1'] != test_data['Production Qty Collect Result_Fill2'])
)

test_equip1 = test_data[categorical_features].eq(0).all(axis=1)
test_equip2 = test_data[categorical_features].eq(1).all(axis=1)
condition_equip_different = ~test_equip1 & ~test_equip2 

# 조건들을 묶어서 필터링
test_condition = ( condition_receip | condition_production_qty | condition_equip_different )

test_abnormal = test_data[test_condition]
# abnormal로 제외하고 남은 데이터

test_filtered = test_data[~test_condition]

# 장비가 0 또는 1의 값으로 나누기 (label encoding으로 Equipment #1: 0 , Equipment #2: 1)
test_model1 = test_filtered[test_filtered[categorical_features].eq(0).all(axis=1)]
test_model2 = test_filtered[test_filtered[categorical_features].eq(1).all(axis=1)]

test_model1_for_prediction = test_model1.drop(columns=['Set ID'])
test_model2_for_prediction = test_model2.drop(columns=['Set ID'])


test_model1_predictions = model1_voting.predict(test_model1_for_prediction)
test_model2_predictions = model2_voting.predict(test_model2_for_prediction)

# 예측을 위한 데이터 인덱스
test_model1_index = test_model1.index
test_model2_index = test_model2.index

# 검증 데이터의 전체 예측을 위한 결과 결합
final_predictions = []

for idx in test_data.index:
    if idx in test_model1_index:
        final_predictions.append(test_model1_predictions[test_model1_index.get_loc(idx)])
    elif idx in test_model2_index:
        final_predictions.append(test_model2_predictions[test_model2_index.get_loc(idx)])
    else:
        final_predictions.append('AbNormal')

In [91]:
for i in range(len(final_predictions)):
    if final_predictions[i] == 0:
        final_predictions[i] = "Normal"
    elif final_predictions[i] == 1:
        final_predictions[i] = "AbNormal"
final_predictions

['Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'AbNormal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'AbNormal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Normal',
 'Norm

### 제출 파일 작성


In [96]:
# 제출 데이터 읽어오기 (df_test는 전처리된 데이터가 저장됨)
df_sub = pd.read_csv("./submission.csv")
df_sub["target"] = final_predictions

# 제출 파일 저장
df_sub.to_csv("./submission_8vs1.csv", index=False)

**우측 상단의 제출 버튼을 클릭해 결과를 확인하세요**


In [93]:
xxx = pd.read_csv("./data/submission.csv")
xxx

Set ID  target
0      OP753345013050000002  Normal
1      OP753345013050000005  Normal
2      OP753345013050000006  Normal
3      OP753345013050000008  Normal
4      OP753345013050000009  Normal
...                     ...     ...
17356  OP753345054040002683  Normal
17357  OP753345054040002685  Normal
17358  OP753345054040002686  Normal
17359  OP753345054040002687  Normal
17360  OP753345054040002689  Normal

[17361 rows x 2 columns]

In [94]:
test_data = pd.read_csv(os.path.join(ROOT_DIR, "test.csv"))
test_data

Set ID Wip Line_Dam Process Desc._Dam  \
0      0001be084fbc4aaa9d921f39e595961b      IVI-OB6     Dam Dispenser   
1      0005bbd180064abd99e63f9ed3e1ac80      IVI-OB6     Dam Dispenser   
2      000948934c4140d883d670adcb609584      IVI-OB6     Dam Dispenser   
3      000a6bfd02874c6296dc7b2e9c5678a7      IVI-OB6     Dam Dispenser   
4      0018e78ce91343678716e2ea27a51c95      IVI-OB6     Dam Dispenser   
...                                 ...          ...               ...   
17356  ffea508b59934d689b540f95eb3fa730      IVI-OB6     Dam Dispenser   
17357  ffed8923c8a448a98afc641b770be153      IVI-OB6     Dam Dispenser   
17358  fff1e73734da40adbe805359b3efb462      IVI-OB6     Dam Dispenser   
17359  fff8e38bdd09470baf95f71e92075dec      IVI-OB6     Dam Dispenser   
17360  fffa83e0a13d4c2db4fd8bf905b517d4      IVI-OB6     Dam Dispenser   

          Equipment_Dam Model.Suffix_Dam Workorder_Dam  Insp. Seq No._Dam  \
0      Dam dispenser #2      AJX75334501    3J1XF767-1                  1   
1      Dam dispenser #2      AJX75334501    4B1XD472-2                  1   
2      Dam dispenser #1      AJX75334501    3H1XE355-1                  1   
3      Dam dispenser #2      AJX75334501    3L1XA128-1                  1   
4      Dam dispenser #1      AJX75334501    4A1XA639-1                  1   
...                 ...              ...           ...                ...   
17356  Dam dispenser #2      AJX75334501    3K1XB597-1                  1   
17357  Dam dispenser #2      AJX75334501    4A1XB974-1                  1   
17358  Dam dispenser #1      AJX75334501    3L1XA998-1                  1   
17359  Dam dispenser #1      AJX75334501    3F1XC376-1                  1   
17360  Dam dispenser #1      AJX75334501    3J1XC756-1                  1   

      Insp Judge Code_Dam  CURE END POSITION X Collect Result_Dam  \
0                      OK                                  1000.0   
1                      OK                                  1000.0   
2                      OK                                   240.0   
3                      OK                                  1000.0   
4                      OK                                   240.0   
...                   ...                                     ...   
17356                  OK                                  1000.0   
17357                  OK                                  1000.0   
17358                  OK                                   240.0   
17359                  OK                                   240.0   
17360                  OK                                   240.0   

       CURE END POSITION X Unit Time_Dam  ...  \
0                                    NaN  ...   
1                                    NaN  ...   
2                                    NaN  ...   
3                                    NaN  ...   
4                                    NaN  ...   
...                                  ...  ...   
17356                                NaN  ...   
17357                                NaN  ...   
17358                                NaN  ...   
17359                                NaN  ...   
17360                                NaN  ...   

       Production Qty Collect Result_Fill2  Production Qty Unit Time_Fill2  \
0                                      195                             NaN   
1                                       14                             NaN   
2                                       98                             NaN   
3                                       14                             NaN   
4                                        1                             NaN   
...                                    ...                             ...   
17356                                   14                             NaN   
17357                                   12                             NaN   
17358                                    4                             NaN   
17359                